In [ ]:
!pip install pycaret[full]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 320 kB 4.0 MB/s 
     |████████████████████████████████| 137 kB 42.3 MB/s 
     |████████████████████████████████| 268 kB 43.0 MB/s 
     |████████████████████████████████| 56 kB 4.4 MB/s 
     |████████████████████████████████| 25.9 MB 54.1 MB/s 
     |████████████████████████████████| 88 kB 7.0 MB/s 
     |████████████████████████████████| 1.3 MB 25.5 MB/s 
     |████████████████████████████████| 3.3 MB 35.8 MB/s 
     |████████████████████████████████| 16.9 MB 1.1 MB/s 
     |████████████████████████████████| 167 kB 61.1 MB/s 
     |████████████████████████████████| 10.4 MB 44.9 MB/s 
     |████████████████████████████████| 2.0 MB 45.0 MB/s 
     |████████████████████████████████| 6.8 MB 14.9 MB/s 
     |████████████████████████████████| 1.7 MB 46.3 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  In

In [ ]:
!pip install surprise

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 11.8 MB 3.7 MB/s 
  Created wheel for scikit-surprise: filename=scikit_surprise-1.1.1-cp37-cp37m-linux_x86_64.whl size=1627556 sha256=f4799ea74ec5e875dfff705720210830647826854135120727e160644955f205
  Stored in directory: /root/.cache/pip/wheels/76/44/74/b498c42be47b2406bd27994e16c5188e337c657025ab400c1c
Successfully built scikit-surprise


In [ ]:
from google.colab import drive 
from pycaret.utils import enable_colab
enable_colab()
drive.mount('/content/drive')

Colab mode enabled.
Mounted at /content/drive


In [ ]:
import numpy as np
import pandas as pd

from pycaret.classification import *

In [ ]:
info_df_TRAIN = pd.read_csv("/content/drive/MyDrive/DSML/Traveldata_Train.csv")
response_df_TRAIN = pd.read_csv("/content/drive/MyDrive/DSML/Surveydata_Train.csv")

info_df_TEST = pd.read_csv("/content/drive/MyDrive/DSML/Traveldata_Test.csv")
response_df_TEST = pd.read_csv("/content/drive/MyDrive/DSML/Surveydata_Test.csv")

In [ ]:
df_TRAIN = info_df_TRAIN.merge(response_df_TRAIN, how='inner', on='ID')
df_TEST = info_df_TEST.merge(response_df_TEST, how='inner', on='ID')
print(df_TRAIN.shape)
print(df_TEST.shape)

(94379, 25)
(35602, 24)


## **Setup 1**
- Imputation:
  - Numeric: Median
  - Categorical: NA
- Encoding:
  - One-Hot Encoding: Gender, Customer_Type, Type_Travel, Travel_Class, Seat_Class 
  - Ordinal Encoding: Seat_Comfort, Arrival_Time_Convenient, Catering, Platform_Location, Onboard_Wifi_Service, Onboard_Entertainment, Online_Support, Ease_of_Online_Booking, Onboard_Service, Legroom, Baggage_Handling, CheckIn_Service, Cleanliness, Online_Boarding 
- Feature Engineering:
  - Feature Interaction
  - Group Features

In [ ]:
preprocess_pipeline_1 = {
    
    # IMPUTATION
    'imputation_type': 'simple', 
    'numeric_imputation': 'median',     
    
    # ENCODING
    'ordinal_features': {
         'Seat_Comfort': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Arrival_Time_Convenient': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Catering': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Platform_Location': ['Very Inconvenient', 'Inconvenient', 'Needs Improvement', 'Manageable', 'Convenient', 'Very Convenient'],
         'Onboard_Wifi_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Onboard_Entertainment': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Online_Support': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Ease_of_Online_Booking': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Onboard_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Legroom': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Baggage_Handling': ['Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'CheckIn_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Cleanliness': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Online_Boarding': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent']
    },
    
    # OUTLIERS
    'remove_outliers': True,
    
    # SCALE
    'normalize': True,
    
    # FE 
    'feature_interaction': True,
    'group_features': [
        ['Seat_Comfort', 'Catering', 'Platform_Location', 'Arrival_Time_Convenient'], 
        ['Onboard_Wifi_Service', 'Onboard_Entertainment', 'Ease_of_Online_Booking', 'Online_Boarding', 'Online_Support'],
        ['Ease_of_Online_Booking', 'Baggage_Handling', 'Onboard_Service', 'Cleanliness', 'Legroom']
    ],
    
    # FS 
    'feature_selection': True, 
    'remove_multicollinearity': True
    
}

In [ ]:
clf_exp_1 = setup(
    data=df_TRAIN, target="Overall_Experience", 
    session_id=12345, fold=5,
    **preprocess_pipeline_1
)

Description               Value
0                               session_id               12345
1                                   Target  Overall_Experience
2                              Target Type              Binary
3                            Label Encoded                None
4                            Original Data         (94379, 25)
5                           Missing Values                True
6                         Numeric Features                   5
7                     Categorical Features                  19
8                         Ordinal Features                True
9                High Cardinality Features               False
10                 High Cardinality Method                None
11                   Transformed Train Set         (62761, 64)
12                    Transformed Test Set         (28314, 64)
13                      Shuffle Train-Test                True
14                     Stratify Train-Test               False
15                          Fold Generator     StratifiedKFold
16                             Fold Number                   5
17                                CPU Jobs                  -1
18                                 Use GPU               False
19                          Log Experiment               False
20                         Experiment Name    clf-default-name
21                                     USI                27d3
22                         Imputation Type              simple
23          Iterative Imputation Iteration                None
24                         Numeric Imputer              median
25      Iterative Imputation Numeric Model                None
26                     Categorical Imputer            constant
27  Iterative Imputation Categorical Model                None
28           Unknown Categoricals Handling      least_frequent
29                               Normalize                True
30                        Normalize Method              zscore
31                          Transformation               False
32                   Transformation Method                None
33                                     PCA               False
34                              PCA Method                None
35                          PCA Components                None
36                     Ignore Low Variance               False
37                     Combine Rare Levels               False
38                    Rare Level Threshold                None
39                         Numeric Binning               False
40                         Remove Outliers                True
41                      Outliers Threshold                0.05
42                Remove Multicollinearity                True
43             Multicollinearity Threshold                 0.9
44             Remove Perfect Collinearity                True
45                              Clustering               False
46                    Clustering Iteration                None
47                     Polynomial Features               False
48                       Polynomial Degree                None
49                    Trignometry Features               False
50                    Polynomial Threshold                None
51                          Group Features                True
52                       Feature Selection                True
53                Feature Selection Method             classic
54            Features Selection Threshold                 0.8
55                     Feature Interaction                True
56                           Feature Ratio               False
57                   Interaction Threshold                0.01
58                           Fix Imbalance               False
59                    Fix Imbalance Method               SMOTE

INFO:logs:create_model_container: 0
INFO:logs:master_model_container: 0
INFO:logs:display_container: 1
INFO:logs:Pipeline(memory=None,
         steps=[('dtypes',
                 DataTypes_Auto_infer(categorical_features=[],
                                      display_types=True, features_todrop=[],
                                      id_columns=['ID'],
                                      ml_usecase='classification',
                                      numerical_features=[],
                                      target='Overall_Experience',
                                      time_features=[])),
                ('imputer',
                 Simple_Imputer(categorical_strategy='not_available',
                                fill_value_categorical=None,
                                fill_value_numerical=No...
                 Fix_multicollinearity(correlation_with_target_preference=None,
                                       correlation_with_target_threshold=0.0,
           

In [ ]:
X_1 = get_config('X')
pipeline_1 = get_config('prep_pipe')

INFO:logs:Initializing get_config()
INFO:logs:get_config(variable=X)
INFO:logs:Global variable: X returned as        Seat_Comfort  group_1_Min  Onboard_Entertainment  \
0               3.0          2.0                    3.0   
1               2.0          2.0                    2.0   
2               3.0          3.0                    5.0   
3               4.0          3.0                    3.0   
4               4.0          3.0                    5.0   
...             ...          ...                    ...   
94374           2.0          2.0                    2.0   
94375           5.0          3.0                    6.0   
94376           3.0          4.0                    6.0   
94377           3.0          3.0                    3.0   
94378           4.0          4.0                    4.0   

       Customer_Type_Loyal Customer  Onboard_Service  Catering  group_0_Max  \
0                               1.0              3.0       6.0          6.0   
1                      

In [ ]:
models_1 = compare_models(n_select=5)

Model  Accuracy     AUC  Recall   Prec.  \
catboost              CatBoost Classifier    0.9549  0.9932  0.9534  0.9649   
xgboost         Extreme Gradient Boosting    0.9536  0.9927  0.9511  0.9648   
lightgbm  Light Gradient Boosting Machine    0.9525  0.9923  0.9497  0.9642   
rf               Random Forest Classifier    0.9505  0.9913  0.9485  0.9619   
et                 Extra Trees Classifier    0.9495  0.9904  0.9484  0.9601   
gbc          Gradient Boosting Classifier    0.9313  0.9844  0.9348  0.9410   
dt               Decision Tree Classifier    0.9229  0.9217  0.9323  0.9290   
knn                K Neighbors Classifier    0.9222  0.9705  0.9275  0.9320   
ada                  Ada Boost Classifier    0.9164  0.9772  0.9217  0.9272   
lr                    Logistic Regression    0.9006  0.9638  0.9171  0.9051   
ridge                    Ridge Classifier    0.8986  0.0000  0.9150  0.9035   
lda          Linear Discriminant Analysis    0.8986  0.9616  0.9150  0.9035   
qda       Quadratic Discriminant Analysis    0.8816  0.9370  0.8779  0.9069   
svm                   SVM - Linear Kernel    0.8702  0.0000  0.8948  0.8768   
nb                            Naive Bayes    0.8400  0.9052  0.8405  0.8672   
dummy                    Dummy Classifier    0.5551  0.5000  1.0000  0.5551   

              F1   Kappa     MCC  TT (Sec)  
catboost  0.9591  0.9088  0.9089    28.468  
xgboost   0.9579  0.9062  0.9063    14.950  
lightgbm  0.9569  0.9040  0.9041     2.494  
rf        0.9551  0.9000  0.9002    10.172  
et        0.9542  0.8978  0.8979     8.898  
gbc       0.9379  0.8610  0.8611    21.950  
dt        0.9306  0.8437  0.8438     1.070  
knn       0.9298  0.8426  0.8427    14.546  
ada       0.9245  0.8308  0.8309     5.186  
lr        0.9110  0.7984  0.7985    12.764  
ridge     0.9092  0.7944  0.7944     0.168  
lda       0.9092  0.7943  0.7944     0.804  
qda       0.8906  0.7615  0.7646     0.474  
svm       0.8844  0.7363  0.7396     2.920  
nb        0.8536  0.6774  0.6778     0.174  
dummy     0.7139  0.0000  0.0000     0.154

INFO:logs:create_model_container: 16
INFO:logs:master_model_container: 16
INFO:logs:display_container: 2
INFO:logs:[<catboost.core.CatBoostClassifier object at 0x7f280b8beb90>, XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, objective='binary:logistic',
              predictor='auto', random_state=12345, reg_alpha=0, ...), LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance

In [ ]:
models_1_score_grid = pull()
models_1_mean, models_1_std = models_1_score_grid['Accuracy'].mean(), models_1_score_grid['Accuracy'].std()
print([models_1_mean - models_1_std, models_1_mean, models_1_mean + models_1_std])

[0.7973745039366885, 0.89365625, 0.9899379960633116]


In [ ]:
choose_models_1 = models_1[0]

In [ ]:
predict_model(choose_models_1);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f280b8beb90>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.     F1   Kappa  \
0  CatBoost Classifier    0.9555  0.9934  0.9526  0.9654  0.959  0.9104   

      MCC  
0  0.9105

In [ ]:
choose_models_1_fn = finalize_model(choose_models_1)

INFO:logs:Initializing finalize_model()
INFO:logs:finalize_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f280b8beb90>, fit_kwargs=None, groups=None, model_only=True, display=None, experiment_custom_tags=None, return_train_score=False)
INFO:logs:Finalizing <catboost.core.CatBoostClassifier object at 0x7f280b8beb90>
INFO:logs:Initializing create_model()
INFO:logs:create_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f280b8beb90>, fold=None, round=4, cross_validation=True, predict=True, fit_kwargs={}, groups=None, refit=True, verbose=False, system=False, metrics=None, experiment_custom_tags=None, add_to_model_list=False, probability_threshold=None, display=None, return_train_score=False, kwargs={})
INFO:logs:Checking exceptions
INFO:logs:Importing libraries
INFO:logs:Copying training dataset
INFO:logs:Defining folds
INFO:logs:Declaring metric variables
INFO:logs:Importing untrained model
INFO:logs:Declaring custom model
INFO:logs:CatBoost Classifier Import

In [ ]:
choose_models_1_pred = predict_model(choose_models_1_fn, data=df_TEST)

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f280bb48090>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


## **Setup 2**
- Imputation:
  - Numeric: Median, Regression
  - Categorical: NA
- Encoding:
  - One-Hot Encoding: Gender, Customer_Type, Type_Travel, Travel_Class, Seat_Class 
  - Ordinal Encoding: Seat_Comfort, Arrival_Time_Convenient, Catering, Platform_Location, Onboard_Wifi_Service, Onboard_Entertainment, Online_Support, Ease_of_Online_Booking, Onboard_Service, Legroom, Baggage_Handling, CheckIn_Service, Cleanliness, Online_Boarding 
- Feature Engineering:
  - Feature Interaction
  - Group Features

In [ ]:
!cp "/content/drive/MyDrive/DSML/categorical_imputation.py" "/content"
!cp "/content/drive/MyDrive/DSML/numeric_imputation.py" "/content"

In [ ]:
from numeric_imputation import replace_with_regression_and_median

In [ ]:
df_TRAIN_regression_and_median = replace_with_regression_and_median(df=df_TRAIN, existed_variables=['Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins'])
df_TEST_regression_and_median = replace_with_regression_and_median(df=df_TEST, existed_variables=['Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins'])

score: 0.932157468408056
coef: [[0.9771727]]
score: 0.9309256405582267
coef: [[0.98315735]]


In [ ]:
print(df_TRAIN_regression_and_median.isnull().sum())
print("-" * 50)
print(df_TEST_regression_and_median.isnull().sum())

ID                            0
Gender                       77
Customer_Type              8951
Age                          33
Type_Travel                9226
Travel_Class                  0
Travel_Distance               0
Departure_Delay_in_Mins       0
Arrival_Delay_in_Mins         0
Overall_Experience            0
Seat_Comfort                 61
Seat_Class                    0
Arrival_Time_Convenient    8930
Catering                   8741
Platform_Location            30
Onboard_Wifi_Service         30
Onboard_Entertainment        18
Online_Support               91
Ease_of_Online_Booking       73
Onboard_Service            7601
Legroom                      90
Baggage_Handling            142
CheckIn_Service              77
Cleanliness                   6
Online_Boarding               6
dtype: int64
--------------------------------------------------
ID                            0
Gender                       30
Customer_Type              3383
Age                          11
Type_Tra

In [ ]:
preprocess_pipeline_2 = {
    
    # IMPUTATION
    'imputation_type': 'simple', 
    'numeric_imputation': 'median',     
    
    # ENCODING
    'ordinal_features': {
         'Seat_Comfort': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Arrival_Time_Convenient': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Catering': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Platform_Location': ['Very Inconvenient', 'Inconvenient', 'Needs Improvement', 'Manageable', 'Convenient', 'Very Convenient'],
         'Onboard_Wifi_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Onboard_Entertainment': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Online_Support': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Ease_of_Online_Booking': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Onboard_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Legroom': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Baggage_Handling': ['Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'CheckIn_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Cleanliness': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Online_Boarding': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent']
    },
    
    # OUTLIERS
    'remove_outliers': True,
    
    # SCALE
    'normalize': True,
    
    # FE 
    'feature_interaction': True,
    'group_features': [
        ['Seat_Comfort', 'Catering', 'Platform_Location', 'Arrival_Time_Convenient'], 
        ['Onboard_Wifi_Service', 'Onboard_Entertainment', 'Ease_of_Online_Booking', 'Online_Boarding', 'Online_Support'],
        ['Ease_of_Online_Booking', 'Baggage_Handling', 'Onboard_Service', 'Cleanliness', 'Legroom']
    ],
    
    # FS 
    'feature_selection': True, 
    'remove_multicollinearity': True
    
}

In [ ]:
clf_exp_2 = setup(
    data=df_TRAIN_regression_and_median, target="Overall_Experience", 
    session_id=12345, fold=5,
    **preprocess_pipeline_2
)

Description               Value
0                               session_id               12345
1                                   Target  Overall_Experience
2                              Target Type              Binary
3                            Label Encoded                None
4                            Original Data         (94379, 25)
5                           Missing Values                True
6                         Numeric Features                   5
7                     Categorical Features                  19
8                         Ordinal Features                True
9                High Cardinality Features               False
10                 High Cardinality Method                None
11                   Transformed Train Set         (62761, 64)
12                    Transformed Test Set         (28314, 64)
13                      Shuffle Train-Test                True
14                     Stratify Train-Test               False
15                          Fold Generator     StratifiedKFold
16                             Fold Number                   5
17                                CPU Jobs                  -1
18                                 Use GPU               False
19                          Log Experiment               False
20                         Experiment Name    clf-default-name
21                                     USI                f9b0
22                         Imputation Type              simple
23          Iterative Imputation Iteration                None
24                         Numeric Imputer              median
25      Iterative Imputation Numeric Model                None
26                     Categorical Imputer            constant
27  Iterative Imputation Categorical Model                None
28           Unknown Categoricals Handling      least_frequent
29                               Normalize                True
30                        Normalize Method              zscore
31                          Transformation               False
32                   Transformation Method                None
33                                     PCA               False
34                              PCA Method                None
35                          PCA Components                None
36                     Ignore Low Variance               False
37                     Combine Rare Levels               False
38                    Rare Level Threshold                None
39                         Numeric Binning               False
40                         Remove Outliers                True
41                      Outliers Threshold                0.05
42                Remove Multicollinearity                True
43             Multicollinearity Threshold                 0.9
44             Remove Perfect Collinearity                True
45                              Clustering               False
46                    Clustering Iteration                None
47                     Polynomial Features               False
48                       Polynomial Degree                None
49                    Trignometry Features               False
50                    Polynomial Threshold                None
51                          Group Features                True
52                       Feature Selection                True
53                Feature Selection Method             classic
54            Features Selection Threshold                 0.8
55                     Feature Interaction                True
56                           Feature Ratio               False
57                   Interaction Threshold                0.01
58                           Fix Imbalance               False
59                    Fix Imbalance Method               SMOTE

INFO:logs:create_model_container: 0
INFO:logs:master_model_container: 0
INFO:logs:display_container: 1
INFO:logs:Pipeline(memory=None,
         steps=[('dtypes',
                 DataTypes_Auto_infer(categorical_features=[],
                                      display_types=True, features_todrop=[],
                                      id_columns=['ID'],
                                      ml_usecase='classification',
                                      numerical_features=[],
                                      target='Overall_Experience',
                                      time_features=[])),
                ('imputer',
                 Simple_Imputer(categorical_strategy='not_available',
                                fill_value_categorical=None,
                                fill_value_numerical=No...
                 Fix_multicollinearity(correlation_with_target_preference=None,
                                       correlation_with_target_threshold=0.0,
           

In [ ]:
X_2 = get_config('X')
pipeline_2 = get_config('prep_pipe')

INFO:logs:Initializing get_config()
INFO:logs:get_config(variable=X)
INFO:logs:Global variable: X returned as        Seat_Comfort  group_1_Min  Onboard_Entertainment  \
0               3.0          2.0                    3.0   
1               2.0          2.0                    2.0   
2               3.0          3.0                    5.0   
3               4.0          3.0                    3.0   
4               4.0          3.0                    5.0   
...             ...          ...                    ...   
94374           2.0          2.0                    2.0   
94375           5.0          3.0                    6.0   
94376           3.0          4.0                    6.0   
94377           3.0          3.0                    3.0   
94378           4.0          4.0                    4.0   

       Customer_Type_Loyal Customer  Onboard_Service  Catering  \
0                               1.0              3.0       6.0   
1                               1.0              

In [ ]:
models_2 = compare_models(n_select=5)

Model  Accuracy     AUC  Recall   Prec.  \
catboost              CatBoost Classifier    0.9547  0.9931  0.9538  0.9642   
xgboost         Extreme Gradient Boosting    0.9528  0.9927  0.9511  0.9634   
lightgbm  Light Gradient Boosting Machine    0.9512  0.9922  0.9484  0.9632   
rf               Random Forest Classifier    0.9497  0.9910  0.9486  0.9602   
et                 Extra Trees Classifier    0.9482  0.9899  0.9480  0.9582   
gbc          Gradient Boosting Classifier    0.9312  0.9840  0.9337  0.9419   
dt               Decision Tree Classifier    0.9252  0.9240  0.9348  0.9308   
knn                K Neighbors Classifier    0.9174  0.9676  0.9232  0.9276   
ada                  Ada Boost Classifier    0.9138  0.9756  0.9229  0.9219   
lr                    Logistic Regression    0.9007  0.9632  0.9175  0.9049   
ridge                    Ridge Classifier    0.8983  0.0000  0.9172  0.9014   
lda          Linear Discriminant Analysis    0.8983  0.9613  0.9171  0.9014   
qda       Quadratic Discriminant Analysis    0.8702  0.9321  0.8572  0.9084   
svm                   SVM - Linear Kernel    0.8588  0.0000  0.9111  0.8532   
nb                            Naive Bayes    0.8401  0.9068  0.8406  0.8671   
dummy                    Dummy Classifier    0.5550  0.5000  1.0000  0.5550   

              F1   Kappa     MCC  TT (Sec)  
catboost  0.9590  0.9084  0.9085    27.834  
xgboost   0.9572  0.9046  0.9047    15.240  
lightgbm  0.9557  0.9015  0.9016     2.130  
rf        0.9544  0.8983  0.8983     9.584  
et        0.9531  0.8952  0.8953     8.254  
gbc       0.9377  0.8609  0.8609    22.338  
dt        0.9328  0.8485  0.8485     1.062  
knn       0.9254  0.8328  0.8328    14.034  
ada       0.9224  0.8255  0.8255     4.916  
lr        0.9111  0.7986  0.7987    12.150  
ridge     0.9092  0.7938  0.7939     0.166  
lda       0.9092  0.7938  0.7939     0.792  
qda       0.8769  0.7400  0.7485     0.410  
svm       0.8783  0.7105  0.7206     2.610  
nb        0.8537  0.6774  0.6778     0.170  
dummy     0.7138  0.0000  0.0000     0.094

INFO:logs:create_model_container: 16
INFO:logs:master_model_container: 16
INFO:logs:display_container: 2
INFO:logs:[<catboost.core.CatBoostClassifier object at 0x7f280b910f90>, XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, objective='binary:logistic',
              predictor='auto', random_state=12345, reg_alpha=0, ...), LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance

In [ ]:
models_2_score_grid = pull()
models_2_mean, models_2_std = models_2_score_grid['Accuracy'].mean(), models_2_score_grid['Accuracy'].std()
print([models_2_mean - models_2_std, models_2_mean, models_2_mean + models_2_std])

[0.7952076835703868, 0.8916, 0.987992316429613]


In [ ]:
choose_models_2 = models_2[0]

In [ ]:
predict_model(choose_models_2);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f280b910f90>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  CatBoost Classifier    0.9557  0.9934  0.9532  0.9653  0.9592  0.9109   

      MCC  
0  0.9109

In [ ]:
choose_models_2_fn = finalize_model(choose_models_2)

INFO:logs:Initializing finalize_model()
INFO:logs:finalize_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f280b910f90>, fit_kwargs=None, groups=None, model_only=True, display=None, experiment_custom_tags=None, return_train_score=False)
INFO:logs:Finalizing <catboost.core.CatBoostClassifier object at 0x7f280b910f90>
INFO:logs:Initializing create_model()
INFO:logs:create_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f280b910f90>, fold=None, round=4, cross_validation=True, predict=True, fit_kwargs={}, groups=None, refit=True, verbose=False, system=False, metrics=None, experiment_custom_tags=None, add_to_model_list=False, probability_threshold=None, display=None, return_train_score=False, kwargs={})
INFO:logs:Checking exceptions
INFO:logs:Importing libraries
INFO:logs:Copying training dataset
INFO:logs:Defining folds
INFO:logs:Declaring metric variables
INFO:logs:Importing untrained model
INFO:logs:Declaring custom model
INFO:logs:CatBoost Classifier Import

In [ ]:
choose_models_2_pred = predict_model(choose_models_2_fn, data=df_TEST_regression_and_median)

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ff4956d0>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


## **Setup 3**
- Imputation:
  - Numeric: Median, MF
  - Categorical: NA
- Encoding:
  - One-Hot Encoding: Gender, Customer_Type, Type_Travel, Travel_Class, Seat_Class 
  - Ordinal Encoding: X
- Feature Engineering:
  - Feature Interaction
  - Group Features

In [ ]:
from categorical_imputation import *

In [ ]:
params = {
    'cid_col': ['ID'],
    'iid_col': [
        'Seat_Comfort', 'Arrival_Time_Convenient', 'Catering', 'Platform_Location', 'Onboard_Wifi_Service',
        'Onboard_Entertainment', 'Online_Support', 'Ease_of_Online_Booking', 'Onboard_Service', 'Legroom',
        'Baggage_Handling', 'CheckIn_Service', 'Cleanliness', 'Online_Boarding'
    ],
    'iid_colname': 'Question',
    'cid_colname': 'ID',
    'response_colname': 'Response',
    'response_map': {
        'Extremely Poor': 0,
        'Very Inconvenient': 0,
        'Poor': 1,
        'Inconvenient': 1,
        'Needs Improvement': 2,
        'Manageable': 3, 
        'Acceptable': 3,
        'Good': 4,
        'Convenient': 4, 
        'Excellent': 5,
        'Very Convenient': 5
    },
    'response_scale': (0, 5),
    'model_params': {
        'lr_all': 0.001, 
        'n_epochs': 100, 
        'n_factors': 300
    }
}

In [ ]:
interaction_df_melted, le, model = create_mf_model(df=df_TRAIN, **params)
interaction_matrix_fn = make_response_prediction(df=interaction_df_melted, le=le, model=model, cid_colname='ID', iid_colname='Question', response_colname='Response')
df_TRAIN_mf_and_median = finalize_matrix_completion(df=df_TRAIN, interaction_df=interaction_matrix_fn, non_iid_cols=['Gender', 'Customer_Type', 'Age', 'Type_Travel', 'Travel_Class', 'Travel_Distance', 'Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins', 'Overall_Experience', 'Seat_Class'])

RMSE: 1.0192


In [ ]:
interaction_df_melted, le, model = create_mf_model(df=df_TEST, **params)
interaction_matrix_fn = make_response_prediction(df=interaction_df_melted, le=le, model=model, cid_colname='ID', iid_colname='Question', response_colname='Response')
df_TEST_mf_and_median = finalize_matrix_completion(df=df_TEST, interaction_df=interaction_matrix_fn, non_iid_cols=['Gender', 'Customer_Type', 'Age', 'Type_Travel', 'Travel_Class', 'Travel_Distance', 'Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins', 'Seat_Class'])

RMSE: 1.0227


In [ ]:
preprocess_pipeline_3 = {
    
    # IMPUTATION
    'imputation_type': 'simple',    
    'numeric_imputation': 'median',  
    
    # ENCODING
    
    # OUTLIERS
    'remove_outliers': True,
    
    # SCALE
    'normalize': True,
    
    # FE 
    'feature_interaction': True,
    'group_features': [
        ['Seat_Comfort', 'Catering', 'Platform_Location', 'Arrival_Time_Convenient'], 
        ['Onboard_Wifi_Service', 'Onboard_Entertainment', 'Ease_of_Online_Booking', 'Online_Boarding', 'Online_Support'],
        ['Ease_of_Online_Booking', 'Baggage_Handling', 'Onboard_Service', 'Cleanliness', 'Legroom']
    ],
    
    # FS 
    'feature_selection': True, 
    'remove_multicollinearity': True
    
}

In [ ]:
clf_exp_3 = setup(
    data=df_TRAIN_mf_and_median, target="Overall_Experience", 
    session_id=12345, fold=5,
    **preprocess_pipeline_3
)

Description               Value
0                               session_id               12345
1                                   Target  Overall_Experience
2                              Target Type              Binary
3                            Label Encoded                None
4                            Original Data         (94379, 25)
5                           Missing Values                True
6                         Numeric Features                  19
7                     Categorical Features                   5
8                         Ordinal Features               False
9                High Cardinality Features               False
10                 High Cardinality Method                None
11                   Transformed Train Set         (62761, 65)
12                    Transformed Test Set         (28314, 65)
13                      Shuffle Train-Test                True
14                     Stratify Train-Test               False
15                          Fold Generator     StratifiedKFold
16                             Fold Number                   5
17                                CPU Jobs                  -1
18                                 Use GPU               False
19                          Log Experiment               False
20                         Experiment Name    clf-default-name
21                                     USI                3f2c
22                         Imputation Type              simple
23          Iterative Imputation Iteration                None
24                         Numeric Imputer              median
25      Iterative Imputation Numeric Model                None
26                     Categorical Imputer            constant
27  Iterative Imputation Categorical Model                None
28           Unknown Categoricals Handling      least_frequent
29                               Normalize                True
30                        Normalize Method              zscore
31                          Transformation               False
32                   Transformation Method                None
33                                     PCA               False
34                              PCA Method                None
35                          PCA Components                None
36                     Ignore Low Variance               False
37                     Combine Rare Levels               False
38                    Rare Level Threshold                None
39                         Numeric Binning               False
40                         Remove Outliers                True
41                      Outliers Threshold                0.05
42                Remove Multicollinearity                True
43             Multicollinearity Threshold                 0.9
44             Remove Perfect Collinearity                True
45                              Clustering               False
46                    Clustering Iteration                None
47                     Polynomial Features               False
48                       Polynomial Degree                None
49                    Trignometry Features               False
50                    Polynomial Threshold                None
51                          Group Features                True
52                       Feature Selection                True
53                Feature Selection Method             classic
54            Features Selection Threshold                 0.8
55                     Feature Interaction                True
56                           Feature Ratio               False
57                   Interaction Threshold                0.01
58                           Fix Imbalance               False
59                    Fix Imbalance Method               SMOTE

INFO:logs:create_model_container: 0
INFO:logs:master_model_container: 0
INFO:logs:display_container: 1
INFO:logs:Pipeline(memory=None,
         steps=[('dtypes',
                 DataTypes_Auto_infer(categorical_features=[],
                                      display_types=True, features_todrop=[],
                                      id_columns=['ID'],
                                      ml_usecase='classification',
                                      numerical_features=[],
                                      target='Overall_Experience',
                                      time_features=[])),
                ('imputer',
                 Simple_Imputer(categorical_strategy='not_available',
                                fill_value_categorical=None,
                                fill_value_numerical=No...
                 Fix_multicollinearity(correlation_with_target_preference=None,
                                       correlation_with_target_threshold=0.0,
           

In [ ]:
models_3 = compare_models(n_select=5)

Model  Accuracy     AUC  Recall   Prec.  \
catboost              CatBoost Classifier    0.9555  0.9932  0.9535  0.9661   
xgboost         Extreme Gradient Boosting    0.9535  0.9926  0.9507  0.9651   
lightgbm  Light Gradient Boosting Machine    0.9527  0.9926  0.9490  0.9653   
rf               Random Forest Classifier    0.9512  0.9913  0.9485  0.9631   
et                 Extra Trees Classifier    0.9503  0.9908  0.9481  0.9619   
gbc          Gradient Boosting Classifier    0.9357  0.9852  0.9348  0.9487   
knn                K Neighbors Classifier    0.9348  0.9770  0.9264  0.9551   
dt               Decision Tree Classifier    0.9237  0.9228  0.9311  0.9317   
ada                  Ada Boost Classifier    0.9202  0.9790  0.9215  0.9341   
lr                    Logistic Regression    0.9025  0.9640  0.9147  0.9102   
svm                   SVM - Linear Kernel    0.8996  0.0000  0.9088  0.9105   
ridge                    Ridge Classifier    0.8966  0.0000  0.9120  0.9029   
lda          Linear Discriminant Analysis    0.8965  0.9605  0.9119  0.9028   
nb                            Naive Bayes    0.8733  0.9421  0.8745  0.8951   
qda       Quadratic Discriminant Analysis    0.7119  0.7077  0.7454  0.7403   
dummy                    Dummy Classifier    0.5558  0.5000  1.0000  0.5558   

              F1   Kappa     MCC  TT (Sec)  
catboost  0.9597  0.9101  0.9102    32.160  
xgboost   0.9578  0.9060  0.9061    15.556  
lightgbm  0.9571  0.9044  0.9046     2.282  
rf        0.9557  0.9013  0.9014     9.384  
et        0.9550  0.8995  0.8996     7.746  
gbc       0.9417  0.8699  0.8701    23.236  
knn       0.9405  0.8686  0.8691   114.716  
dt        0.9314  0.8456  0.8456     1.084  
ada       0.9277  0.8387  0.8388     4.678  
lr        0.9125  0.8023  0.8024     3.022  
svm       0.9096  0.7967  0.7968     0.562  
ridge     0.9074  0.7903  0.7903     0.136  
lda       0.9074  0.7902  0.7902     0.860  
nb        0.8847  0.7442  0.7444     0.148  
qda       0.7422  0.4156  0.4166     0.384  
dummy     0.7145  0.0000  0.0000     0.088

INFO:logs:create_model_container: 16
INFO:logs:master_model_container: 16
INFO:logs:display_container: 2
INFO:logs:[<catboost.core.CatBoostClassifier object at 0x7f27ec3b44d0>, XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, objective='binary:logistic',
              predictor='auto', random_state=12345, reg_alpha=0, ...), LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance

In [ ]:
models_3_score_grid = pull()
models_3_mean, models_3_std = models_3_score_grid['Accuracy'].mean(), models_3_score_grid['Accuracy'].std()
print([models_3_mean - models_3_std, models_3_mean, models_3_mean + models_3_std])

[0.7819801588902086, 0.8883624999999999, 0.9947448411097913]


In [ ]:
choose_models_3 = models_3[0]

In [ ]:
predict_model(choose_models_3);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ec3b44d0>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall  Prec.      F1   Kappa    MCC
0  CatBoost Classifier    0.9558  0.9936  0.9535  0.965  0.9593  0.9109  0.911

In [ ]:
choose_models_3_fn = finalize_model(choose_models_3)

INFO:logs:Initializing finalize_model()
INFO:logs:finalize_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ec3b44d0>, fit_kwargs=None, groups=None, model_only=True, display=None, experiment_custom_tags=None, return_train_score=False)
INFO:logs:Finalizing <catboost.core.CatBoostClassifier object at 0x7f27ec3b44d0>
INFO:logs:Initializing create_model()
INFO:logs:create_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ec3b44d0>, fold=None, round=4, cross_validation=True, predict=True, fit_kwargs={}, groups=None, refit=True, verbose=False, system=False, metrics=None, experiment_custom_tags=None, add_to_model_list=False, probability_threshold=None, display=None, return_train_score=False, kwargs={})
INFO:logs:Checking exceptions
INFO:logs:Importing libraries
INFO:logs:Copying training dataset
INFO:logs:Defining folds
INFO:logs:Declaring metric variables
INFO:logs:Importing untrained model
INFO:logs:Declaring custom model
INFO:logs:CatBoost Classifier Import

In [ ]:
choose_models_3_pred = predict_model(choose_models_3_fn, data=df_TEST_mf_and_median)

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ebb17590>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


## **Setup 4**
- Imputation:
  - Numeric: Iterative
  - Categorical: Iterative
- Encoding:
  - One-Hot Encoding: Gender, Customer_Type, Type_Travel, Travel_Class, Seat_Class 
  - Ordinal Encoding: Seat_Comfort, Arrival_Time_Convenient, Catering, Platform_Location, Onboard_Wifi_Service, Onboard_Entertainment, Online_Support, Ease_of_Online_Booking, Onboard_Service, Legroom, Baggage_Handling, CheckIn_Service, Cleanliness, Online_Boarding 
- Feature Engineering:
  - Feature Interaction
  - Group Features

In [ ]:
preprocess_pipeline_4 = {
    
    # IMPUTATION
    'imputation_type': 'iterative',    
    
    # ENCODING
    'ordinal_features': {
         'Seat_Comfort': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Arrival_Time_Convenient': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Catering': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Platform_Location': ['Very Inconvenient', 'Inconvenient', 'Needs Improvement', 'Manageable', 'Convenient', 'Very Convenient'],
         'Onboard_Wifi_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Onboard_Entertainment': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Online_Support': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Ease_of_Online_Booking': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Onboard_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Legroom': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Baggage_Handling': ['Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'CheckIn_Service': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Cleanliness': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent'],
         'Online_Boarding': ['Extremely Poor', 'Poor', 'Needs Improvement', 'Acceptable', 'Good', 'Excellent']
    },
    
    # OUTLIERS
    'remove_outliers': True,
    
    # SCALE
    'normalize': True,
    
    # FE 
    'feature_interaction': True,
    'group_features': [
        ['Seat_Comfort', 'Catering', 'Platform_Location', 'Arrival_Time_Convenient'], 
        ['Onboard_Wifi_Service', 'Onboard_Entertainment', 'Ease_of_Online_Booking', 'Online_Boarding', 'Online_Support'],
        ['Ease_of_Online_Booking', 'Baggage_Handling', 'Onboard_Service', 'Cleanliness', 'Legroom']
    ],
    
    # FS 
    'feature_selection': True, 
    'remove_multicollinearity': True
    
}

In [ ]:
clf_exp_4 = setup(
    data=df_TRAIN, target="Overall_Experience", 
    session_id=12345, fold=5,
    **preprocess_pipeline_4
)

Description                            Value
0                               session_id                            12345
1                                   Target               Overall_Experience
2                              Target Type                           Binary
3                            Label Encoded                             None
4                            Original Data                      (94379, 25)
5                           Missing Values                             True
6                         Numeric Features                                5
7                     Categorical Features                               19
8                         Ordinal Features                             True
9                High Cardinality Features                            False
10                 High Cardinality Method                             None
11                   Transformed Train Set                      (62761, 58)
12                    Transformed Test Set                      (28314, 58)
13                      Shuffle Train-Test                             True
14                     Stratify Train-Test                            False
15                          Fold Generator                  StratifiedKFold
16                             Fold Number                                5
17                                CPU Jobs                               -1
18                                 Use GPU                            False
19                          Log Experiment                            False
20                         Experiment Name                 clf-default-name
21                                     USI                             a1f8
22                         Imputation Type                        iterative
23          Iterative Imputation Iteration                                5
24                         Numeric Imputer                             mean
25      Iterative Imputation Numeric Model  Light Gradient Boosting Machine
26                     Categorical Imputer                         constant
27  Iterative Imputation Categorical Model  Light Gradient Boosting Machine
28           Unknown Categoricals Handling                   least_frequent
29                               Normalize                             True
30                        Normalize Method                           zscore
31                          Transformation                            False
32                   Transformation Method                             None
33                                     PCA                            False
34                              PCA Method                             None
35                          PCA Components                             None
36                     Ignore Low Variance                            False
37                     Combine Rare Levels                            False
38                    Rare Level Threshold                             None
39                         Numeric Binning                            False
40                         Remove Outliers                             True
41                      Outliers Threshold                             0.05
42                Remove Multicollinearity                             True
43             Multicollinearity Threshold                              0.9
44             Remove Perfect Collinearity                             True
45                              Clustering                            False
46                    Clustering Iteration                             None
47                     Polynomial Features                            False
48                       Polynomial Degree                             None
49                    Trignometry Features                            False
50                    Polynomial Threshold                             None
51                          Group Features                             True
52 

INFO:logs:create_model_container: 0
INFO:logs:master_model_container: 0
INFO:logs:display_container: 1
INFO:logs:Pipeline(memory=None,
         steps=[('dtypes',
                 DataTypes_Auto_infer(categorical_features=[],
                                      display_types=True, features_todrop=[],
                                      id_columns=['ID'],
                                      ml_usecase='classification',
                                      numerical_features=[],
                                      target='Overall_Experience',
                                      time_features=[])),
                ('imputer',
                 Iterative_Imputer(add_indicator=False,
                                   classifier=LGBMClassifier(boosting_type='gbdt',
                                                             class_weight=None,...
                 Fix_multicollinearity(correlation_with_target_preference=None,
                                       correlation_with_t

In [ ]:
X_4 = get_config('X')
pipeline_4 = get_config('prep_pipe')

INFO:logs:Initializing get_config()
INFO:logs:get_config(variable=X)
INFO:logs:Global variable: X returned as        Seat_Comfort  group_1_Min  Onboard_Entertainment  \
0               3.0          2.0                    3.0   
1               2.0          2.0                    2.0   
2               3.0          3.0                    5.0   
3               4.0          3.0                    3.0   
4               4.0          3.0                    5.0   
...             ...          ...                    ...   
94374           2.0          2.0                    2.0   
94375           5.0          3.0                    6.0   
94376           3.0          4.0                    6.0   
94377           3.0          3.0                    3.0   
94378           4.0          4.0                    4.0   

       Customer_Type_Loyal Customer  Onboard_Service  Catering  group_0_Max  \
0                               1.0              3.0       6.0          6.0   
1                      

In [ ]:
models_4 = compare_models(n_select=5)

Model  Accuracy     AUC  Recall   Prec.  \
catboost              CatBoost Classifier    0.9559  0.9933  0.9535  0.9667   
xgboost         Extreme Gradient Boosting    0.9541  0.9929  0.9499  0.9669   
lightgbm  Light Gradient Boosting Machine    0.9529  0.9926  0.9474  0.9671   
rf               Random Forest Classifier    0.9509  0.9911  0.9467  0.9643   
et                 Extra Trees Classifier    0.9498  0.9905  0.9468  0.9624   
gbc          Gradient Boosting Classifier    0.9337  0.9851  0.9330  0.9470   
dt               Decision Tree Classifier    0.9278  0.9269  0.9355  0.9347   
knn                K Neighbors Classifier    0.9232  0.9715  0.9238  0.9372   
ada                  Ada Boost Classifier    0.9154  0.9766  0.9187  0.9283   
lr                    Logistic Regression    0.8962  0.9628  0.9076  0.9059   
ridge                    Ridge Classifier    0.8906  0.0000  0.8947  0.9073   
lda          Linear Discriminant Analysis    0.8906  0.9597  0.8946  0.9073   
qda       Quadratic Discriminant Analysis    0.8737  0.9320  0.8638  0.9060   
svm                   SVM - Linear Kernel    0.8640  0.0000  0.8880  0.8735   
nb                            Naive Bayes    0.8494  0.9188  0.8459  0.8787   
dummy                    Dummy Classifier    0.5558  0.5000  1.0000  0.5558   

              F1   Kappa     MCC  TT (Sec)  
catboost  0.9600  0.9108  0.9109    27.834  
xgboost   0.9583  0.9072  0.9074    13.466  
lightgbm  0.9571  0.9048  0.9050     2.018  
rf        0.9554  0.9008  0.9010     8.658  
et        0.9545  0.8986  0.8988     8.154  
gbc       0.9399  0.8660  0.8661    21.056  
dt        0.9351  0.8538  0.8538     0.984  
knn       0.9304  0.8448  0.8449    12.456  
ada       0.9235  0.8288  0.8289     4.688  
lr        0.9067  0.7898  0.7898    11.664  
ridge     0.9009  0.7789  0.7790     0.158  
lda       0.9009  0.7789  0.7790     0.710  
qda       0.8829  0.7460  0.7494     0.390  
svm       0.8790  0.7235  0.7275     2.824  
nb        0.8620  0.6965  0.6971     0.158  
dummy     0.7145  0.0000  0.0000     0.092

INFO:logs:create_model_container: 16
INFO:logs:master_model_container: 16
INFO:logs:display_container: 2
INFO:logs:[<catboost.core.CatBoostClassifier object at 0x7f27ea332550>, XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, objective='binary:logistic',
              predictor='auto', random_state=12345, reg_alpha=0, ...), LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance

In [ ]:
models_4_score_grid = pull()
models_4_mean, models_4_std = models_4_score_grid['Accuracy'].mean(), models_4_score_grid['Accuracy'].std()
print([models_4_mean - models_4_std, models_4_mean, models_4_mean + models_4_std])

[0.7964945551323631, 0.8927499999999999, 0.9890054448676368]


In [ ]:
choose_models_4 = models_4[0]

In [ ]:
predict_model(choose_models_4);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ea332550>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.      F1   Kappa  \
0  CatBoost Classifier    0.9569  0.9938  0.9532  0.9675  0.9603  0.9133   

      MCC  
0  0.9134

In [ ]:
choose_models_4_fn = finalize_model(choose_models_4)

INFO:logs:Initializing finalize_model()
INFO:logs:finalize_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ea332550>, fit_kwargs=None, groups=None, model_only=True, display=None, experiment_custom_tags=None, return_train_score=False)
INFO:logs:Finalizing <catboost.core.CatBoostClassifier object at 0x7f27ea332550>
INFO:logs:Initializing create_model()
INFO:logs:create_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ea332550>, fold=None, round=4, cross_validation=True, predict=True, fit_kwargs={}, groups=None, refit=True, verbose=False, system=False, metrics=None, experiment_custom_tags=None, add_to_model_list=False, probability_threshold=None, display=None, return_train_score=False, kwargs={})
INFO:logs:Checking exceptions
INFO:logs:Importing libraries
INFO:logs:Copying training dataset
INFO:logs:Defining folds
INFO:logs:Declaring metric variables
INFO:logs:Importing untrained model
INFO:logs:Declaring custom model
INFO:logs:CatBoost Classifier Import

In [ ]:
choose_models_4_pred = predict_model(choose_models_4_fn, data=df_TEST)

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27e9beb4d0>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor
INFO:logs:Iterative Imputation: 1 cycle | Online_Boarding
INFO:logs:Iterative Imputation: 1 cycle | Cleanliness
INFO:logs:Iterative Imputation: 1 cycle | Onboard_Entertainment
INFO:logs:Iterative Imputation: 1 cycle | Age
INFO:logs:Iterative Imputation: 1 cycle | Platform_Location
INFO:logs:Iterative Imputation: 1 cycle | Onboard_Wifi_Service
INFO:logs:Iterative Imputation: 1 cycle | Ease_of_Online_Booking
INFO:logs:Iterative Imputation: 1 cycle | CheckIn_Service
INFO:logs:Iterative Imputation: 1 cycle | Seat_Comfort
INFO:logs:Iterative Imputation: 1 cycle | Legroom
INFO:logs:Iterat

## **Setup 5**
- Imputation:
  - Numeric: Regression, Iterative, MF
  - Categorical: Iterative
- Encoding:
  - One-Hot Encoding: Gender, Customer_Type, Type_Travel, Travel_Class, Seat_Class 
  - Ordinal Encoding: X 
- Feature Engineering:
  - Feature Interaction
  - Group Features

In [ ]:
from numeric_imputation import replace_with_regression

In [ ]:
df_TRAIN_regression = replace_with_regression(df=df_TRAIN, existed_variables=['Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins'])
df_TEST_regression = replace_with_regression(df=df_TEST, existed_variables=['Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins'])

score: 0.932157468408056
coef: [[0.9771727]]
score: 0.9309256405582267
coef: [[0.98315735]]


In [ ]:
interaction_df_melted, le, model = create_mf_model(df=df_TRAIN_regression, **params)
interaction_matrix_fn = make_response_prediction(df=interaction_df_melted, le=le, model=model, cid_colname='ID', iid_colname='Question', response_colname='Response')
df_TRAIN_preprocessed = finalize_matrix_completion(df=df_TRAIN_regression, interaction_df=interaction_matrix_fn, non_iid_cols=['Gender', 'Customer_Type', 'Age', 'Type_Travel', 'Travel_Class', 'Travel_Distance', 'Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins', 'Overall_Experience', 'Seat_Class'])

RMSE: 1.0192


In [ ]:
interaction_df_melted, le, model = create_mf_model(df=df_TEST_regression, **params)
interaction_matrix_fn = make_response_prediction(df=interaction_df_melted, le=le, model=model, cid_colname='ID', iid_colname='Question', response_colname='Response')
df_TEST_preprocessed = finalize_matrix_completion(df=df_TEST_regression, interaction_df=interaction_matrix_fn, non_iid_cols=['Gender', 'Customer_Type', 'Age', 'Type_Travel', 'Travel_Class', 'Travel_Distance', 'Departure_Delay_in_Mins', 'Arrival_Delay_in_Mins', 'Seat_Class'])

RMSE: 1.0227


In [ ]:
preprocess_pipeline_5 = {
    
    # IMPUTATION
    'imputation_type': 'iterative',    
    
    # ENCODING
    
    # OUTLIERS
    'remove_outliers': True,
    
    # SCALE
    'normalize': True,
    
    # FE 
    'feature_interaction': True,
    'group_features': [
        ['Seat_Comfort', 'Catering', 'Platform_Location', 'Arrival_Time_Convenient'], 
        ['Onboard_Wifi_Service', 'Onboard_Entertainment', 'Ease_of_Online_Booking', 'Online_Boarding', 'Online_Support'],
        ['Ease_of_Online_Booking', 'Baggage_Handling', 'Onboard_Service', 'Cleanliness', 'Legroom']
    ],
    
    # FS 
    'feature_selection': True, 
    'remove_multicollinearity': True
    
}

In [ ]:
clf_exp_5 = setup(
    data=df_TRAIN_preprocessed, target="Overall_Experience", 
    session_id=12345, fold=5,
    **preprocess_pipeline_5
)

Description                            Value
0                               session_id                            12345
1                                   Target               Overall_Experience
2                              Target Type                           Binary
3                            Label Encoded                             None
4                            Original Data                      (94379, 25)
5                           Missing Values                             True
6                         Numeric Features                               19
7                     Categorical Features                                5
8                         Ordinal Features                            False
9                High Cardinality Features                            False
10                 High Cardinality Method                             None
11                   Transformed Train Set                      (62761, 60)
12                    Transformed Test Set                      (28314, 60)
13                      Shuffle Train-Test                             True
14                     Stratify Train-Test                            False
15                          Fold Generator                  StratifiedKFold
16                             Fold Number                                5
17                                CPU Jobs                               -1
18                                 Use GPU                            False
19                          Log Experiment                            False
20                         Experiment Name                 clf-default-name
21                                     USI                             83dc
22                         Imputation Type                        iterative
23          Iterative Imputation Iteration                                5
24                         Numeric Imputer                             mean
25      Iterative Imputation Numeric Model  Light Gradient Boosting Machine
26                     Categorical Imputer                         constant
27  Iterative Imputation Categorical Model  Light Gradient Boosting Machine
28           Unknown Categoricals Handling                   least_frequent
29                               Normalize                             True
30                        Normalize Method                           zscore
31                          Transformation                            False
32                   Transformation Method                             None
33                                     PCA                            False
34                              PCA Method                             None
35                          PCA Components                             None
36                     Ignore Low Variance                            False
37                     Combine Rare Levels                            False
38                    Rare Level Threshold                             None
39                         Numeric Binning                            False
40                         Remove Outliers                             True
41                      Outliers Threshold                             0.05
42                Remove Multicollinearity                             True
43             Multicollinearity Threshold                              0.9
44             Remove Perfect Collinearity                             True
45                              Clustering                            False
46                    Clustering Iteration                             None
47                     Polynomial Features                            False
48                       Polynomial Degree                             None
49                    Trignometry Features                            False
50                    Polynomial Threshold                             None
51                          Group Features                             True
52 

INFO:logs:create_model_container: 0
INFO:logs:master_model_container: 0
INFO:logs:display_container: 1
INFO:logs:Pipeline(memory=None,
         steps=[('dtypes',
                 DataTypes_Auto_infer(categorical_features=[],
                                      display_types=True, features_todrop=[],
                                      id_columns=['ID'],
                                      ml_usecase='classification',
                                      numerical_features=[],
                                      target='Overall_Experience',
                                      time_features=[])),
                ('imputer',
                 Iterative_Imputer(add_indicator=False,
                                   classifier=LGBMClassifier(boosting_type='gbdt',
                                                             class_weight=None,...
                 Fix_multicollinearity(correlation_with_target_preference=None,
                                       correlation_with_t

In [ ]:
X_5 = get_config('X')
pipeline_5 = get_config('prep_pipe')

In [ ]:
models_5 = compare_models(n_select=5)

Model  Accuracy     AUC  Recall   Prec.  \
catboost              CatBoost Classifier    0.9565  0.9934  0.9543  0.9672   
xgboost         Extreme Gradient Boosting    0.9544  0.9931  0.9517  0.9660   
lightgbm  Light Gradient Boosting Machine    0.9540  0.9928  0.9508  0.9660   
rf               Random Forest Classifier    0.9511  0.9915  0.9485  0.9631   
et                 Extra Trees Classifier    0.9500  0.9907  0.9482  0.9615   
gbc          Gradient Boosting Classifier    0.9363  0.9858  0.9383  0.9468   
knn                K Neighbors Classifier    0.9335  0.9766  0.9253  0.9539   
dt               Decision Tree Classifier    0.9246  0.9234  0.9339  0.9308   
ada                  Ada Boost Classifier    0.9188  0.9789  0.9243  0.9295   
lr                    Logistic Regression    0.9094  0.9684  0.9215  0.9163   
svm                   SVM - Linear Kernel    0.9064  0.0000  0.9125  0.9189   
lda          Linear Discriminant Analysis    0.9045  0.9656  0.9233  0.9068   
ridge                    Ridge Classifier    0.9044  0.0000  0.9234  0.9066   
nb                            Naive Bayes    0.8788  0.9469  0.8633  0.9142   
qda       Quadratic Discriminant Analysis    0.6946  0.7111  0.5651  0.8375   
dummy                    Dummy Classifier    0.5567  0.5000  1.0000  0.5567   

              F1   Kappa     MCC  TT (Sec)  
catboost  0.9607  0.9121  0.9122    31.950  
xgboost   0.9588  0.9079  0.9080    14.822  
lightgbm  0.9584  0.9070  0.9071     2.416  
rf        0.9558  0.9012  0.9013     8.944  
et        0.9548  0.8990  0.8991     7.182  
gbc       0.9425  0.8710  0.8711    20.148  
knn       0.9394  0.8659  0.8664   117.794  
dt        0.9324  0.8471  0.8471     0.960  
ada       0.9269  0.8356  0.8356     4.382  
lr        0.9189  0.8163  0.8164     2.582  
svm       0.9157  0.8106  0.8107     0.558  
lda       0.9150  0.8061  0.8062     0.764  
ridge     0.9149  0.8059  0.8061     0.130  
nb        0.8880  0.7562  0.7577     0.142  
qda       0.6730  0.4054  0.4350     0.368  
dummy     0.7152  0.0000  0.0000     0.090

INFO:logs:create_model_container: 16
INFO:logs:master_model_container: 16
INFO:logs:display_container: 2
INFO:logs:[<catboost.core.CatBoostClassifier object at 0x7f27eafe69d0>, XGBClassifier(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, objective='binary:logistic',
              predictor='auto', random_state=12345, reg_alpha=0, ...), LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance

In [ ]:
models_5_score_grid = pull()
models_5_mean, models_5_std = models_5_score_grid['Accuracy'].mean(), models_5_score_grid['Accuracy'].std()
print([models_5_mean - models_5_std, models_5_mean, models_5_mean + models_5_std])

[0.7811453459936688, 0.889625, 0.9981046540063312]


In [ ]:
choose_models_5 = models_5[0]

In [ ]:
predict_model(choose_models_5);

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27eafe69d0>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor


Model  Accuracy     AUC  Recall   Prec.     F1   Kappa  \
0  CatBoost Classifier    0.9577  0.9938  0.9543  0.9677  0.961  0.9148   

      MCC  
0  0.9149

In [ ]:
choose_models_5_fn = finalize_model(choose_models_5)

INFO:logs:Initializing finalize_model()
INFO:logs:finalize_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27eafe69d0>, fit_kwargs=None, groups=None, model_only=True, display=None, experiment_custom_tags=None, return_train_score=False)
INFO:logs:Finalizing <catboost.core.CatBoostClassifier object at 0x7f27eafe69d0>
INFO:logs:Initializing create_model()
INFO:logs:create_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27eafe69d0>, fold=None, round=4, cross_validation=True, predict=True, fit_kwargs={}, groups=None, refit=True, verbose=False, system=False, metrics=None, experiment_custom_tags=None, add_to_model_list=False, probability_threshold=None, display=None, return_train_score=False, kwargs={})
INFO:logs:Checking exceptions
INFO:logs:Importing libraries
INFO:logs:Copying training dataset
INFO:logs:Defining folds
INFO:logs:Declaring metric variables
INFO:logs:Importing untrained model
INFO:logs:Declaring custom model
INFO:logs:CatBoost Classifier Import

In [ ]:
choose_models_5_pred = predict_model(choose_models_5_fn, data=df_TEST_preprocessed)

INFO:logs:Initializing predict_model()
INFO:logs:predict_model(estimator=<catboost.core.CatBoostClassifier object at 0x7f27ec764690>, probability_threshold=None, encoded_labels=False, drift_report=False, raw_score=False, round=4, verbose=True, ml_usecase=MLUsecase.CLASSIFICATION, display=None, drift_kwargs=None)
INFO:logs:Checking exceptions
INFO:logs:Preloading libraries
INFO:logs:Preparing display monitor
INFO:logs:Iterative Imputation: 1 cycle | Age
INFO:logs:Iterative Imputation: 1 cycle | Arrival_Delay_in_Mins
INFO:logs:Iterative Imputation: 1 cycle | Departure_Delay_in_Mins
INFO:logs:Iterative Imputation: 1 cycle | Gender
INFO:logs:Iterative Imputation: 1 cycle | Customer_Type
INFO:logs:Iterative Imputation: 1 cycle | Type_Travel
INFO:logs:Iterative Imputation: 1 cycle | Age
INFO:logs:Iterative Imputation: 1 cycle | Arrival_Delay_in_Mins
INFO:logs:Iterative Imputation: 1 cycle | Departure_Delay_in_Mins
INFO:logs:Iterative Imputation: 1 cycle | Gender
INFO:logs:Iterative Imputatio